In [1]:
%cd ..
%load_ext autoreload
%autoreload 2

RTS_DATA = "/mnt/d/rts/"
METADATA = RTS_DATA + 'metadata'
VIDEOS = RTS_DATA + '0'
REMOTE_VIDEOS = "/mnt/rts"
OUTDIR = 'data'



/home/kikohs/work/rts


In [2]:
from datetime import datetime
import orjson
import pandas as pd
import zipfile
import os
import io
from typing import Dict, List, Optional, Tuple

In [3]:
# LOCAL imports
import rts

LOG = rts.utils.get_logger()

In [ ]:
# vidx = rts.ingest.read_video_folder_index(os.path.join(OUTDIR, 'vidx.json'))
# df = rts.ingest.read_all_metadata(METADATA, vidx)
# rts.ingest.metadata_to_hdf5(OUTDIR, 'rts_metadata', df)

df = rts.ingest.load_metadata_hdf5(OUTDIR, 'rts_metadata')

In [ ]:
client = rts.db.fulltext.get_client()
midx = rts.db.fulltext.get_or_create_media_index(client)
midx.get_stats().number_of_documents

In [ ]:
#TODO get unique geo, people, for the whole media

In [ ]:
a = df.groupby('collection')['collection'].count().sort_values(ascending=False)
a.to_csv(os.path.join(OUTDIR, 'collections.csv'))

In [ ]:
a = df.groupby('contentType')['contentType'].count().sort_values(ascending=False)
a.to_csv(os.path.join(OUTDIR, 'contentType.csv'))

In [ ]:
midx.delete_all_documents()

In [ ]:
rts.db.fulltext.index_media(df, midx)

In [ ]:
import whisper

model = whisper.load_model("base")
# result = model.transcribe("audio.mp3")
# print(result["text"])

In [ ]:
df.publishedBy.apply(lambda x: len(x) if x else 0).unique()

In [ ]:
# midx = rts.db.meilisearch.get_or_create_media_index(client)
midx.get_stats().number_of_documents

In [ ]:
import av

In [ ]:
import time

import av
import av.datasets


print("Decoding with default (slice) threading...")

container = av.open(
    av.datasets.curated("pexels/time-lapse-video-of-night-sky-857195.mp4")
)

start_time = time.time()
for packet in container.demux():
    print(packet)
    for frame in packet.decode():
        print(frame)

default_time = time.time() - start_time
container.close()


print("Decoding with auto threading...")

container = av.open(
    av.datasets.curated("pexels/time-lapse-video-of-night-sky-857195.mp4")
)

# !!! This is the only difference.
container.streams.video[0].thread_type = "AUTO"

start_time = time.time()
for packet in container.demux():
    print(packet)
    for frame in packet.decode():
        print(frame)

auto_time = time.time() - start_time
container.close()


print("Decoded with default threading in {:.2f}s.".format(default_time))
print("Decoded with auto threading in {:.2f}s.".format(auto_time))

In [ ]:
input_ = av.open(av.datasets.curated("pexels/time-lapse-video-of-night-sky-857195.mp4"))
# output = av.open("remuxed.mkv", "w")

# Make an output stream using the input as a template. This copies the stream
# setup from one to the other.
in_stream = input_.streams.video[0]

In [ ]:
in_stream.container

In [ ]:
%ls {VIDEOS}

In [4]:
video_part = os.path.join(VIDEOS, '0', '0', 'ZB001000')
v, a = rts.io.archive.get_video_audio_parts(video_part)



In [11]:
import av
input_ = av.open(a)

In [15]:
input_.streams.audio[0]

<av.AudioStream #0 aac at 48000Hz, mono, fltp at 0x7f04b8e00c70>

In [16]:
output_ = av.open(os.path.join(OUTDIR, 'audio.aac'), 'w')
out_stream = output_.add_stream(template=input_.streams.audio[0])

In [18]:
for packet in input_.demux(input_.streams.audio[0]):

    print(packet)

    # We need to skip the "flushing" packets that `demux` generates.
    if packet.dts is None:
        continue

    # We need to assign the packet to the new stream.
    packet.stream = out_stream

    output_.mux(packet)

input_.close()
output_.close()

<av.Packet of #0, dts=-2048, pts=-2048; 6 bytes at 0x7f04b917dcc0>
<av.Packet of #0, dts=-1024, pts=-1024; 136 bytes at 0x7f04b8e772c0>
<av.Packet of #0, dts=0, pts=0; 175 bytes at 0x7f04b917dcc0>
<av.Packet of #0, dts=1024, pts=1024; 176 bytes at 0x7f04b8e772c0>
<av.Packet of #0, dts=2048, pts=2048; 156 bytes at 0x7f04b917dcc0>
<av.Packet of #0, dts=3072, pts=3072; 135 bytes at 0x7f04b8e772c0>
<av.Packet of #0, dts=4096, pts=4096; 146 bytes at 0x7f04b917dcc0>
<av.Packet of #0, dts=5120, pts=5120; 137 bytes at 0x7f04b8e772c0>
<av.Packet of #0, dts=6144, pts=6144; 174 bytes at 0x7f04b917dcc0>
<av.Packet of #0, dts=7168, pts=7168; 149 bytes at 0x7f04b8e772c0>
<av.Packet of #0, dts=8192, pts=8192; 139 bytes at 0x7f04b917dcc0>
<av.Packet of #0, dts=9216, pts=9216; 135 bytes at 0x7f04b8e772c0>
<av.Packet of #0, dts=10240, pts=10240; 171 bytes at 0x7f04b917dcc0>
<av.Packet of #0, dts=11264, pts=11264; 178 bytes at 0x7f04b8e772c0>
<av.Packet of #0, dts=12288, pts=12288; 193 bytes at 0x7f04b91

In [5]:
rts.io.media.to_wav(a, os.path.join(OUTDIR, 'audio.wav'))

'data/audio.wav'